# Import and function define

In [2]:
from astral import LocationInfo
from astral.sun import sun, azimuth, elevation, golden_hour, blue_hour, SunDirection
from datetime import datetime
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import numpy as np
from geopy.geocoders import Nominatim
from geopy.distance import geodesic
from scipy.optimize import minimize
import json

EXIF_DATE_FMT = "%Y:%m:%d %H:%M:%S"

T0 = 24
T1 = 365.25*T0

def get_loc_info(longitude, latitude):
    geolocator = Nominatim(user_agent="bot")
    location = geolocator.reverse("%f, %f" % (latitude, longitude), language="en")
    return location

# activation function
def activation(x, x0=0, scale=1):
    return 1. / (1 + np.exp(-scale*(x-x0)))

def elevation_from_loc(longitude, latitude, time):
    return np.array([elevation(LocationInfo(longitude=longitude, latitude=latitude).observer, dt) for dt in time])

# loss function
def f(pos, y, sampled_utc):
    longitude, latitude = pos
    y_hat = activation(elevation_from_loc(longitude, latitude, sampled_utc))
    # RMSE of activation function to observed data
    return np.mean(np.sum((y-y_hat)**2))

# callback to get evolution
def trace_callback(x):
    global i
    loss = f(x, activated_el, sampled_utc) 
    d = {"longitude":x[0], "latitude":x[1], "loss":loss, "iter": i}
    print(d)
    opt_traces.append(d)
    i += 1
    return False


def plot_res(_res, _loc):
    print("Estimated location:")
    print(_res.x[0], _res.x[1])
    print(get_loc_info(_res.x[0], _res.x[1]))
    print()
    print("Real location:")
    print(_loc.longitude, _loc.latitude)
    print(get_loc_info(_loc.longitude, _loc.latitude))

    print()
    x_missed = geodesic([_res.x[0], loc.latitude], (_loc.longitude, _loc.latitude)).km
    y_missed = geodesic([loc.longitude, _res.x[1]], (_loc.longitude, _loc.latitude)).km
    print(f"Missed by {geodesic(_res.x, (_loc.longitude, _loc.latitude)).km:.03f} km!")
    print(f"  longitudinal error : {x_missed:.03f} km")
    print(f"  latitudinal error : {y_missed:.03f} km")

    df = pd.DataFrame.from_records(opt_traces)
    fig = px.scatter_geo(df, lat="latitude", lon="longitude", hover_name="iter", color="loss", projection="natural earth", template="plotly_dark")
    fig.add_trace(go.Scattergeo(lat=[_loc.latitude], lon=[_loc.longitude], name="groundtruth", marker={"color":"green", "symbol":"star-diamond-dot"}))
    fig.show()


class DictObject(object):
    def __init__(self, iterable=(), **kwargs):
       self.__dict__.update(iterable, **kwargs)


In [3]:

# Groundtruth
def plot_groundtruth(longitude, latitude, start, end, fig=None, name=""):
    loc = LocationInfo("dummy", latitude=latitude, longitude=longitude)
    image_shooting_utc = pd.date_range(start=start, end=end, freq="H")
    el = elevation_from_loc(loc.longitude, loc.latitude, image_shooting_utc)

    df = pd.DataFrame(index=image_shooting_utc, data=el, columns=[name+' elevation'])
    df[name+" activation"] = df[name+' elevation'].apply(activation)

    if fig is None:
        fig = px.line(df)
    else:
        fig.add_trace(go.Scatter(x=image_shooting_utc, y=el, name=name+" elevation"))
        fig.add_trace(go.Scatter(x=image_shooting_utc, y=df[name+" activation"], name=name+" activation"))
    print(loc.name, loc.latitude, loc.longitude, loc.timezone)
    
    return fig

# First tests

## Synthetic data

In this part I generate some synthetic data : a set of `SAMPLES` points at random dates in a given period, with values equals to the groundtruth day/night activation function with addded gaussian noise and a clip to [0,1].

In [16]:
SAMPLES = 200
image_shooting_utc = pd.date_range("2022-01-01", "2022-12-31", freq="1H").tz_localize("UTC")
loc = LocationInfo("dummy", latitude=50, longitude=15)

# sampling some data for location estimation
sampled_utc = np.random.choice(image_shooting_utc, SAMPLES)
# observed data
activated_el = activation(elevation_from_loc(loc.longitude, loc.latitude, sampled_utc))
# add gaussian noise
activated_el += np.random.normal(0, 0.1, len(activated_el))
activated_el = np.clip(activated_el, 0, 1)
fig = go.Figure()
fig.add_trace(go.Scatter(x=sampled_utc, y=activated_el, mode='markers', name="activated_el"))
fig.update_layout(
    title="observed data (with noise)"
)
fig.show()

In [17]:
# start position, guess
x0 = [0, 0]
# minimization
opt_traces = []
i = 0
res = minimize(f, x0, args=(activated_el, sampled_utc), method='BFGS', callback=trace_callback)
plot_res(res, loc)
fig = plot_groundtruth(loc.longitude, loc.latitude, sorted(sampled_utc)[0], sorted(sampled_utc)[-1], name="groundtruth")
plot_groundtruth(res.x[0], res.x[1], sorted(sampled_utc)[0], sorted(sampled_utc)[-1], name="computed", fig=fig)
fig.add_trace(go.Scatter(x=sampled_utc, y=activated_el, mode='markers', name="input_data"))


{'longitude': 0.8639878034591675, 'latitude': 0.5157667398452759, 'loss': 9.328011106563194, 'iter': 0}
{'longitude': 1.637552312227308, 'latitude': 1.3584306326807225, 'loss': 8.879022228703974, 'iter': 1}
{'longitude': 2.0459891155956553, 'latitude': 2.4053140933914414, 'loss': 8.641283996522212, 'iter': 2}
{'longitude': 3.4242947386060267, 'latitude': 12.071045886554726, 'loss': 6.991136754138548, 'iter': 3}
{'longitude': 8.119217593249552, 'latitude': 45.69283140802846, 'loss': 3.3579918756750273, 'iter': 4}
{'longitude': 8.010110297924061, 'latitude': 44.80958617349171, 'loss': 3.3082869127698347, 'iter': 5}
{'longitude': 13.17628944142453, 'latitude': 50.95598917757731, 'loss': 1.3582245553013514, 'iter': 6}
{'longitude': 14.592771103536663, 'latitude': 50.60085707389497, 'loss': 1.1265602431649875, 'iter': 7}
{'longitude': 14.37095712957165, 'latitude': 48.725437130037534, 'loss': 1.0909582932367934, 'iter': 8}
{'longitude': 14.450473421159476, 'latitude': 49.10649210171614, 'lo

dummy 50.0 15.0 Europe/London
dummy 49.54385324453246 14.692144617730598 Europe/London


What is remarkable in this simulation is the low number of points needed to reach a near perfect loaction! 200 points over 1 year to get as close as 60km from real location.

Would I get the same accuracy given a shorter period of time?

My guess is that the precision comes from the fact that there is equal chance of having day and night observations. I would say that with 95% of sample points observing day (as in most of our timelapse) we would get less precision.

## Real data, 5k points

Here I extracted 5000 data points from a random (outdoor, long term) photoset.

In [18]:
with open("sun_test.json") as fh:
    md = json.load(fh)
sampled_utc = np.array([datetime.strptime(md["images"][im]["image_shooting"], EXIF_DATE_FMT) for im in md["images"]])
activated_el = np.array([md["images"][im]["attributes"]["daylight"] for im in md["images"]])

FileNotFoundError: [Errno 2] No such file or directory: 'sun_test.json'

In [61]:
# start position, guess
x0 = [5, 40]
# minimization
opt_traces = []
i = 0
res = minimize(f, x0, args=(activated_el, sampled_utc), method='BFGS', callback=trace_callback)


{'longitude': 5.97716729478271, 'latitude': 40.25542920351253, 'loss': 131.79451630478096, 'iter': 0}
{'longitude': 8.369721828536802, 'latitude': 40.336451070571265, 'loss': 102.90416801438118, 'iter': 1}
{'longitude': 11.234988871944784, 'latitude': 44.42196429503192, 'loss': 91.80978642357468, 'iter': 2}
{'longitude': 10.30754643198554, 'latitude': 43.639804031873325, 'loss': 89.48668409810384, 'iter': 3}
{'longitude': 10.419176346734853, 'latitude': 43.05242466831516, 'loss': 89.38801911092686, 'iter': 4}
{'longitude': 10.407967627007471, 'latitude': 43.351174994643145, 'loss': 89.32964781811783, 'iter': 5}
{'longitude': 10.413154741129473, 'latitude': 43.34344699414737, 'loss': 89.32935416617049, 'iter': 6}
{'longitude': 10.424888181029166, 'latitude': 43.3272433695422, 'loss': 89.32887102649819, 'iter': 7}
{'longitude': 10.445215844448217, 'latitude': 43.30091841029702, 'loss': 89.32856472843041, 'iter': 8}
{'longitude': 10.444810698973509, 'latitude': 43.302312740991326, 'loss':

In [62]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=sampled_utc, y=activated_el))
fig.show()

In [63]:
plot_res(res)

Estimated location:
10.445149576519631 43.30291691734162
Italy

Real location:
5.7210753 45.177573
Capuche Boules Association, Piste des Jeux Olympiques, Foch Aigle Libération, Secteur 4, Grenoble, Isère, Auvergne-Rhône-Alpes, Metropolitan France, 38100, France

Missed by 561.820 km!


# Real data part 2 : UGA 2k dataset

In [19]:
from pathlib import Path
import json
uga_dir = Path("/media/Tom/Dev/Python/UGA/")
data_dir = uga_dir / "data_2k_bis/"
all_photosets = {}
# for file in data_dir.iterdir():
for file in [data_dir / "1ab73e07.json", data_dir / "0a16502f.json", data_dir / "3e3c3bf2.json"]:
    if file.suffix in [".json"]:
        with open(file) as fh:
            data = json.load(fh)
            pid = data["photo_set"]["id"]
        all_photosets[pid] = data

In [20]:
photosets_info = [{
    "id": k,
    "tz":  v["photo_set"]["tz"],
    "latitude": v["photo_set"]["gps"]["latitude"],
    "longitude": v["photo_set"]["gps"]["longitude"],
    "altitude": v["photo_set"]["gps"]["altitude"],
    }
    for k,v in all_photosets.items()]
# photosetd_df = pd.DataFrame.from_dict(photosets_info, orient="index")
print(photosets_info)

[{'id': 22043, 'tz': 'Europe/Luxembourg', 'latitude': 49.494650552218744, 'longitude': 5.977592932867855, 'altitude': 0.0}, {'id': 32589, 'tz': 'Europe/Paris', 'latitude': 48.8315477, 'longitude': 2.5287305, 'altitude': 0.0}, {'id': 33715, 'tz': 'Asia/Kolkata', 'latitude': 18.4849396, 'longitude': 73.9512284, 'altitude': 0.0}]


Perform minimization on one selected photoset

In [21]:
test_idx = 0
photoset_id = photosets_info[test_idx]["id"]

print(photosets_info[test_idx])

# test data
df = pd.DataFrame.from_records(
    [
        { 
            "photoset_id": pid,
            "image_shooting": datetime.fromisoformat(img["image_shooting"]+"+00:00"),
            "daylight": img["attributes"]["daylight"],
            "brightness": img["brightness"]/128,
        }  
        for pid,pinfo in all_photosets.items() for img in pinfo["photo_set"]["photos"]
    ])
filtered_df = df[df.photoset_id == photoset_id]

# optim raw data
sampled_utc = filtered_df["image_shooting"]
activated_el = filtered_df["daylight"].values

# groundtruth
loc = DictObject(photosets_info[test_idx])

# start position, guess
x0 = [45, 10]
# minimization
opt_traces = []
i = 0
res = minimize(f, x0, args=(activated_el, sampled_utc), method='BFGS', callback=trace_callback)

{'id': 22043, 'tz': 'Europe/Luxembourg', 'latitude': 49.494650552218744, 'longitude': 5.977592932867855, 'altitude': 0.0}
{'longitude': 6.929417280441648, 'latitude': 8.439585796987878, 'loss': 129.3393315156919, 'iter': 0}
{'longitude': 3.87795020432346, 'latitude': 9.425956884050844, 'loss': 120.85983431230248, 'iter': 1}
{'longitude': 12.59149038703205, 'latitude': 27.36182270197371, 'loss': 92.03000956006541, 'iter': 2}
{'longitude': 8.69023998243963, 'latitude': 28.595868493050343, 'loss': 58.583410363957945, 'iter': 3}
{'longitude': 6.4190476054948995, 'latitude': 46.112536277197506, 'loss': 18.303949210702093, 'iter': 4}
{'longitude': 4.287519039173917, 'latitude': 47.83541826380251, 'loss': 16.88260901146778, 'iter': 5}
{'longitude': 4.2558336286519545, 'latitude': 45.33677825413918, 'loss': 15.908441544413956, 'iter': 6}
{'longitude': 4.961110338134849, 'latitude': 45.76645488382254, 'loss': 15.55723030701423, 'iter': 7}
{'longitude': 4.769303033839157, 'latitude': 45.70742901

Plot results of the minimization and groundtruth

In [22]:
fig = plot_groundtruth(loc.longitude, loc.latitude, sorted(sampled_utc)[0], sorted(sampled_utc)[-1], name="groundtruth")
fig = plot_groundtruth(res.x[0], res.x[1], sorted(sampled_utc)[0], sorted(sampled_utc)[-1], fig=fig, name="computed")
fig.add_trace(go.Scatter(x=sampled_utc, y=activated_el, mode='markers', name="input_data"))
fig.show()
plot_res(res, loc)

dummy 49.494650552218744 5.977592932867855 Europe/London
dummy 45.71553115059029 4.79441258104179 Europe/London


Estimated location:
4.79441258104179 45.71553115059029
Rue du Colonel Sebbane, La Glacière, Oullins, Lyon, Métropole de Lyon, Departemental constituency of Rhône, Auvergne-Rhône-Alpes, Metropolitan France, 69600, France

Real location:
5.977592932867855 49.494650552218744
45, Rue du Canal, Brill, Esch-sur-Alzette, Canton Esch-sur-Alzette, 4050, Luxembourg

Missed by 438.798 km!
  longitudinal error : 130.841 km
  latitudinal error : 418.417 km


## Compare theoretical values

 elevation / activation values for 2 positions

In [124]:
fig = plot_groundtruth(0, 0, "2022-01-01", "2022-12-31")
fig = plot_groundtruth(0, 15, "2022-01-01", "2022-12-31", fig)
fig.show()

dummy 0.0 0.0 Europe/London
dummy 15.0 0.0 Europe/London
